# TensorFlow Graph visualizer code

In [1]:
import numpy as np
from IPython.display import clear_output, Image, display, HTML

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = b"<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script src="//cdnjs.cloudflare.com/ajax/libs/polymer/0.3.3/platform.js"></script>
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))

# load model from .pb file

In [2]:
import tensorflow as tf
from tensorflow.python.platform import gfile

def load_pb_model(pb_path):
    with tf.Graph().as_default() as graph:
        with gfile.FastGFile(model_path, 'rb') as f:
            graph_def = tf.GraphDef()
            graph_def.ParseFromString(f.read())
            tf.import_graph_def(graph_def)
            return graph

/Users/yzq/anaconda3/envs/tensorflow/lib/python3.6/importlib/_bootstrap.py:205: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


In [3]:
model_path = './inception/models/classify_image_graph_def.pb'
graph = load_pb_model(model_path)

show_graph(graph.as_graph_def())

# load model from checkpoint

In [4]:
def load_model_from_checkpoint(ckpt_path):
    meta_path = tf.train.latest_checkpoint(ckpt_path) + ".meta"
    sess = tf.Session()
    saver = tf.train.import_meta_graph(meta_path)
    saver.restore(sess, tf.train.latest_checkpoint(ckpt_path))
    return sess

In [5]:
ckpt_path = './checkpoint'
sess = load_model_from_checkpoint(ckpt_path)

INFO:tensorflow:Restoring parameters from ./checkpoint/model.ckpt


In [6]:
show_graph(sess.graph.as_graph_def())

# load model with tf.saved_model api

In [7]:
def load_saved_model(model_path, sess):
    tf.saved_model.loader.load(sess, [tf.saved_model.tag_constants.SERVING], model_path)
    return sess

In [8]:
tf.reset_default_graph()
sess = tf.Session()
model_path = './saved_model/'
sess = load_saved_model(model_path, sess)

INFO:tensorflow:Restoring parameters from b'./saved_model/variables/variables'


In [9]:
show_graph(sess.graph.as_graph_def())